In [15]:
from IPython.display import Audio
import os
import pandas as pd
import eyed3
import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPooling2D
from keras.optimizers import SGD
from keras.layers import LeakyReLU

from ast import literal_eval

import numpy as np
import librosa
import tempfile
import subprocess
import soundfile as sf

import torch.utils.data

import nussl
from IPython.display import Audio
import IPython
from common import viz

import matplotlib.pyplot as plt

from scipy.io import wavfile

from enum import Enum
import gc
import ctypes

import pickle

import tensorflow as tf

from keras.layers import Dense, Dropout, Flatten, Conv2D, MaxPooling2D, Concatenate
from keras.layers import LeakyReLU
from keras import Input, Model

import math

from sklearn.preprocessing import MinMaxScaler, StandardScaler

In [20]:
HOP_SIZE = 256
WINDOW_SIZE = 1024
SAMPLING_RATE = 22050

# Data loading

In [21]:
data_path_orig = 'D:\\lpnu\\магістратура\\диплом\\musdb18'
data_path_wav = 'D:\\lpnu\\магістратура\\диплом\\musdb18_wav'

In [22]:
# class syntax
class Channel(Enum):
    MIXTURE = 0
    DRUMS = 1
    BASS = 2
    OTHER = 3
    VOCALS = 4

In [23]:
def to_wav(path, sr):
    with tempfile.TemporaryDirectory() as tmpdir:
        for subdir in ('train', 'test'):
            origin_dir = os.path.join(path, subdir)
            files = [f for f in os.listdir(origin_dir)
                     if os.path.splitext(f)[1] == '.mp4']
            for file in files:
                path = os.path.join(origin_dir, file)
                name = os.path.splitext(file)[0]
                wav_data = []
                # Extract & save the sound of `ch` channel to a temp directory
                # and then concatenate all channels to a single .wav file
                for ch in range(5):
                    temp_fn = f'{name}.{ch}.wav'
                    out_path = os.path.join(tmpdir, temp_fn)
                    subprocess.run(['ffmpeg', '-i', path,
                                    '-map', f'0:{ch}', out_path])
                    sound, _ = librosa.load(out_path, sr=sr, mono=True)
                    wav_data.append(sound)
                wav_data = np.stack(wav_data, axis=1)
                out_path = os.path.join(
                    data_path_wav, subdir, f'{name}.wav')
                sf.write(out_path, wav_data, sr)

In [24]:
def load_df(path, subdir):
    # Initialize lists to store information
    file_paths = []
    file_names = []
    music_length = []
    sample_rates = []
    music_variations = []

    # Define the directory to search for files
    origin_dir = os.path.join(path, subdir)

    # Iterate through files in the directory and its subdirectories
    for root, _, files in os.walk(origin_dir):
        for file in files:
            if file.endswith(".wav"):
                file_path = os.path.join(root, file)
                file_paths.append(file_path)
                file_names.append(file)

                # Read the WAV file using wavfile.read
                audio_data, sample_rate = librosa.load(file_path, sr=None, mono=False, duration=60)
                sample_rates.append(sample_rate)
                
                music_length.append(librosa.get_duration(y=audio_data[0], sr=sample_rate))
                #print(type(audio_data[0])
                
                # Append the 5 music variations to the list
                music_variations.append(audio_data.T.astype(np.float32))
                
                del file_path, audio_data, sample_rate
                gc.collect()

    # Create a DataFrame from the collected information
    df = pd.DataFrame({
        'File_Path': file_paths,
        'File_Name': file_names,
        'Music_Length': music_length,
        'Sample_Rate': sample_rates,
    })

    # Add columns for each music variation
    for i in range(5):
        """Output .wav files contain 5 channels
        - `0` - The mixture,
        - `1` - The drums,
        - `2` - The bass,
        - `3` - The rest of the accompaniment,
        - `4` - The vocals.
        """
        df[Channel(i).name] = [variation[:, i] for variation in music_variations]
    
    del file_paths, file_names,sample_rates, music_variations
    gc.collect()
    return df

In [ ]:
df_train = load_df(data_path_wav, 'train')
df_train.head()

In [8]:
#df_train.to_pickle('dataset_60.pkl')

In [25]:
gc.collect()

34

In [26]:
def get_stft(audio_data, sr=22050, win_length=1024, hop_length=256):
    spec = librosa.stft(audio_data, hop_length=hop_length, n_fft=win_length )
    print(spec.shape)
    db = librosa.amplitude_to_db(np.abs(spec),ref=np.max)
    gc.collect()
    return spec.astype(np.float32), db.astype(np.float32)

In [27]:
def plot_stft(audio_data, sr=22050, win_length=1024, hop_length=256, cmap='viridis'):
    plt.figure(figsize=(12, 8))
    
    spec, db = get_stft(audio_data, sr, win_length, hop_length)
    #print(len(audio_data))
    #print(db.T.shape)
    librosa.display.specshow(db, sr=sr, hop_length=hop_length, n_fft=win_length, y_axis='log', x_axis='time')
    #display(Audio(data=librosa.istft(spec.astype(np.complex64), hop_length=hop_length, n_fft=win_length), rate=sr))
    
    #spec = np.abs(librosa.stft(audio_data, hop_length=hop_length, win_length=win_length))
    #librosa.display.specshow(spec, sr=sr, hop_length=hop_length, win_length=win_length, y_axis='log', x_axis='time')
    plt.show()

In [28]:
def show_example(df, n, m = None):
    if m == None or m < n:
        m = n+1
    
    for i in range(n,m):
        for j in range(5):
            display(Audio(data=df_train[Channel(j).name][i], rate=df_train['Sample_Rate'][i]))
            plot_stft(df_train[Channel(j).name][i], df_train['Sample_Rate'][i], WINDOW_SIZE, HOP_SIZE)
            
    gc.collect()

In [10]:
show_example(df_train, 4)

NameError: name 'df_train' is not defined

In [29]:
gc.collect()

0

In [30]:
df_train.info(memory_usage = "deep")

NameError: name 'df_train' is not defined

# Preprocessing

## Append STFT to each sample

In [31]:
def create_stft_df(df, sr=22050, win_length=1024, hop_length=256, threshold=0.6):
    df_new = pd.DataFrame(index=range(100))
    for index in range(5):
        df_new[Channel(index).name+'_STFT_SPEC'] = None
        if index != 0:
            df_new[Channel(index).name+'_STFT_MASK'] = None
        #df_new[Channel(i).name+'_STFT_DB'] = None
        print(Channel(index).name)
        for j, song in df[Channel(index).name].items():
            spec, _ = get_stft(song, sr, win_length, hop_length)
            df_new.at[j, Channel(index).name+'_STFT_SPEC'] = spec
            if index != 0:
                mixture_magnitude = df_new['MIXTURE_STFT_SPEC'][j]
                mask = (np.abs(spec) > threshold * np.abs(mixture_magnitude))
                df_new.at[j, Channel(index).name+'_STFT_MASK'] = mask
            gc.collect()
    
    #df[Channel(i).name+'_STFT_SPEC'], df[Channel(i).name+'_STFT_DB'] = spec_list, db_list
    #df_new.to_pickle(Channel(i).name+'_60.pkl')
    return df_new

In [32]:
def sliding_window_middle(lst, n=25):
    result = []
    lst_len = len(lst)

    for i in range(lst_len):
        window = []
        for j in range(n):
            idx = i - n // 2 + j
            if idx < 0:
                window.append(lst[0])
            elif idx >= lst_len:
                window.append(lst[-1])
            else:
                window.append(lst[idx])
        result.append(window)

    return np.array(result)

In [9]:
new_df = pd.read_pickle("stft_dataset_60.pkl")
new_df['MIXTURE_STFT_SPEC'][0].shape

(513, 5168)

In [34]:
display(Audio(data=librosa.istft(new_df['VOCALS_STFT_SPEC'][4].astype(np.complex64), hop_length=HOP_SIZE, n_fft=WINDOW_SIZE), rate=SAMPLING_RATE))
display(Audio(data=librosa.istft(new_df['MIXTURE_STFT_SPEC'][4].astype(np.complex64) * new_df['VOCALS_STFT_MASK'][4].astype(np.complex64), hop_length=HOP_SIZE, n_fft=WINDOW_SIZE), rate=SAMPLING_RATE))

for column in new_df.columns:
    if column == 'MIXTURE_STFT_SPEC':
        print('special ' + column)
        new_df[column] = new_df[column].apply( lambda row: row.T )
        #new_df[column] = new_df[column].apply( lambda row: np.transpose(sliding_window_middle(row.T, 25), (0, 2, 1)) )
        
    else:
        print('general ' + column)
        new_df[column] = new_df[column].apply( lambda row: row.T )

In [33]:
final_df = pd.read_pickle("processed_stft_dataset_60.pkl")
final_df.head()

song                            MIXTURE_STFT_SPEC_FRAME   
0     0  [[0.08187551, 0.08187551, 0.08187551, 0.081875...  \
1     0  [[0.08187551, 0.08187551, 0.08187551, 0.081875...   
2     0  [[0.08187551, 0.08187551, 0.08187551, 0.081875...   
3     0  [[0.08187551, 0.08187551, 0.08187551, 0.081875...   
4     0  [[0.08187551, 0.08187551, 0.08187551, 0.081875...   

                                   MIXTURE_STFT_SPEC   
0  [0.08187551, -0.039624352, -0.09744032, 0.1758...  \
1  [0.02099112, -0.05037343, 0.15608908, -0.15295...   
2  [-0.019724187, 0.08562425, -0.059673235, -0.00...   
3  [0.104797766, -0.16177715, -0.062321976, 0.426...   
4  [0.04130258, 0.057702698, -0.12649705, 0.23361...   

                                     DRUMS_STFT_SPEC   
0  [-0.13781065, 0.11601338, -0.099702515, 0.1310...  \
1  [-0.093082085, 0.051523156, 0.014298474, 0.028...   
2  [0.025637366, -0.034471016, 0.03638204, -0.005...   
3  [0.02763855, -0.015976176, 0.026399914, -0.012...   
4  [0.014516203, 0.031562813, -0.03556164, 0.0517...   

                                     DRUMS_STFT_MASK   
0  [True, True, True, True, False, False, True, F...  \
1  [True, True, False, False, True, False, False,...   
2  [True, False, True, True, False, False, True, ...   
3  [False, False, False, False, True, False, Fals...   
4  [False, False, False, False, False, True, True...   

                                      BASS_STFT_SPEC   
0  [0.061865356, -0.037738383, -0.07464109, 0.114...  \
1  [0.012805708, -0.008471004, 0.113808446, -0.19...   
2  [-0.011532948, 0.032295976, 0.033474654, -0.09...   
3  [0.008272192, -0.035989296, -0.069708414, 0.22...   
4  [-0.011546084, 0.056976188, -0.08417205, 0.078...   

                                      BASS_STFT_MASK   
0  [True, True, True, True, False, False, False, ...  \
1  [True, False, True, True, False, False, False,...   
2  [False, False, False, True, False, False, True...   
3  [False, False, True, False, True, False, True,...   
4  [False, True, True, False, False, True, True, ...   

                                     OTHER_STFT_SPEC   
0  [-0.12170316, 0.1113022, -0.07313652, 0.043905...  \
1  [-0.052231297, -0.0037337795, 0.013689819, 0.0...   
2  [-0.025236372, -0.016057238, 0.0007926887, 0.0...   
3  [-0.0042298534, -0.0045507574, -0.12787597, 0....   
4  [-0.010939419, -0.0013286052, 0.010512196, 0.0...   

                                     OTHER_STFT_MASK   
0  [True, True, True, False, True, True, False, T...  \
1  [True, False, False, False, False, False, True...   
2  [True, False, False, True, True, True, True, T...   
3  [False, False, True, True, True, True, False, ...   
4  [False, False, False, False, True, True, True,...   

                                    VOCALS_STFT_SPEC   
0  [0.2613147, -0.23052862, 0.1712135, -0.1329069...  \
1  [0.09884239, -0.0468765, -0.003971828, -0.0588...   
2  [-0.06994903, 0.12758866, -0.1216005, 0.033696...   
3  [0.014726582, -0.07033248, 0.09275338, -0.0346...   
4  [0.002939146, -0.006491047, -0.011330597, 0.01...   

                                    VOCALS_STFT_MASK  
0  [True, True, True, True, False, False, False, ...  
1  [True, True, False, False, False, False, False...  
2  [True, True, True, True, False, False, False, ...  
3  [False, False, True, False, False, False, Fals...  
4  [False, False, False, False, False, False, Tru...

In [34]:
final_df.info(memory_usage = "deep")

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 486419 entries, 0 to 486418
Data columns (total 11 columns):
 #   Column                   Non-Null Count   Dtype 
---  ------                   --------------   ----- 
 0   song                     486419 non-null  int64 
 1   MIXTURE_STFT_SPEC_FRAME  486419 non-null  object
 2   MIXTURE_STFT_SPEC        486419 non-null  object
 3   DRUMS_STFT_SPEC          486419 non-null  object
 4   DRUMS_STFT_MASK          486419 non-null  object
 5   BASS_STFT_SPEC           486419 non-null  object
 6   BASS_STFT_MASK           486419 non-null  object
 7   OTHER_STFT_SPEC          486419 non-null  object
 8   OTHER_STFT_MASK          486419 non-null  object
 9   VOCALS_STFT_SPEC         486419 non-null  object
 10  VOCALS_STFT_MASK         486419 non-null  object
dtypes: int64(1), object(10)
memory usage: 567.8 MB


In [35]:
final_df['MIXTURE_STFT_SPEC_FRAME'][0].shape

(513, 25)

## Get audio from df example

In [38]:
grouped_df = final_df[final_df['song'] == 4]
np.column_stack(grouped_df['MIXTURE_STFT_SPEC'])

array([[-1.1907870e-02, -1.6808245e-02, -1.8785570e-02, ...,
        -3.2240078e+00, -2.7388964e+00,  3.7480111e+00],
       [ 8.8386759e-03,  7.1674902e-03,  9.1638975e-03, ...,
         1.5254050e+00,  8.7067378e-01,  1.0254976e+00],
       [-3.9225100e-03,  5.5063195e-03, -5.1448988e-03, ...,
         2.1971664e+00,  5.8298368e+00, -1.1146628e+01],
       ...,
       [ 1.5687844e-04, -1.4363401e-04,  6.3876811e-05, ...,
        -2.1323338e-04,  2.0962550e-04, -4.5859762e-02],
       [-1.7513076e-04,  2.4870229e-05,  9.8522483e-05, ...,
         2.0902137e-04, -2.3486125e-04, -1.4289884e-03],
       [ 1.4813824e-04,  1.3235249e-05, -2.1522373e-04, ...,
        -5.1533585e-05,  6.0068964e-05,  4.5763798e-02]], dtype=float32)

In [39]:
grouped_df['MIXTURE_STFT_SPEC'].shape

(5168,)

In [ ]:
display(Audio(data=librosa.istft(np.column_stack(grouped_df['MIXTURE_STFT_SPEC']).astype(np.complex64), hop_length=HOP_SIZE, n_fft=WINDOW_SIZE), rate=SAMPLING_RATE)) 

# CNN for music source isolation

## Test model for vocal detection

In [26]:
model = Sequential()
model.add(Conv2D(16, (3,3), padding='same', input_shape=(513, 25, 1)))
model.add(LeakyReLU())
model.add(Conv2D(16, (3,3), padding='same'))
model.add(LeakyReLU())
model.add(MaxPooling2D(pool_size=(3,3)))
model.add(Dropout(0.25))
model.add(Conv2D(16, (3,3), padding='same'))
model.add(LeakyReLU())
model.add(Conv2D(16, (3,3), padding='same'))
model.add(LeakyReLU())
model.add(MaxPooling2D(pool_size=(3,3)))
model.add(Dropout(0.25))
model.add(Flatten())
model.add(Dense(64))
model.add(LeakyReLU())
model.add(Dropout(0.5))
model.add(Dense(1, activation='sigmoid'))
sgd = SGD(lr=0.001, decay=1e-6, momentum=0.9, nesterov=True)
model.compile(loss=keras.losses.binary_crossentropy, optimizer=sgd, metrics=['accuracy'])

C:\Users\Orest\AppData\Roaming\Python\Python310\site-packages\keras\optimizers\legacy\gradient_descent.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)


In [27]:
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 conv2d (Conv2D)             (None, 513, 25, 16)       160       
                                                                 
 leaky_re_lu (LeakyReLU)     (None, 513, 25, 16)       0         
                                                                 
 conv2d_1 (Conv2D)           (None, 513, 25, 16)       2320      
                                                                 
 leaky_re_lu_1 (LeakyReLU)   (None, 513, 25, 16)       0         
                                                                 
 max_pooling2d (MaxPooling2D  (None, 171, 8, 16)       0         
 )                                                               
                                                                 
 dropout (Dropout)           (None, 171, 8, 16)        0         
                                                        

## Data extraction for testing

In [45]:
model.fit(X, y, epochs=50, batch_size=100)

Epoch 1/50
148/148 [==============================] - 48s 323ms/step - loss: 0.0319 - accuracy: 0.9957
Epoch 2/50
148/148 [==============================] - 48s 325ms/step - loss: 0.0109 - accuracy: 1.0000
Epoch 3/50
148/148 [==============================] - 51s 346ms/step - loss: 0.0070 - accuracy: 1.0000
Epoch 4/50
148/148 [==============================] - 50s 336ms/step - loss: 0.0043 - accuracy: 1.0000
Epoch 5/50
148/148 [==============================] - 49s 334ms/step - loss: 0.0027 - accuracy: 1.0000
Epoch 6/50
148/148 [==============================] - 50s 336ms/step - loss: 0.0018 - accuracy: 1.0000
Epoch 7/50
148/148 [==============================] - 50s 339ms/step - loss: 0.0013 - accuracy: 1.0000
Epoch 8/50
148/148 [==============================] - 50s 339ms/step - loss: 9.5551e-04 - accuracy: 1.0000
Epoch 9/50
148/148 [==============================] - 50s 338ms/step - loss: 7.0549e-04 - accuracy: 1.0000
Epoch 10/50
148/148 [==============================] - 50s 340ms/

KeyboardInterrupt: 

In [ ]:
_, accuracy = model.evaluate(X, y)
print('Accuracy: %.2f' % (accuracy*100))

## Vocal isolation

In [4]:
class dataGenerator(tf.keras.utils.Sequence):
    def __init__(self,file_path, X_column, Y_column, batch_size):
        self.file_path = file_path
        self.X_column = X_column
        self.Y_column = Y_column
        self.batch_size = batch_size
        self.data = pd.read_pickle(file_path)
        self.scaler = StandardScaler()
        
    def __getitem__(self,idx):
        low = idx * self.batch_size
        high = min(low + self.batch_size, self.data.shape[0])
        
        X = np.stack(self.data[self.X_column][int(low):int(high)])
        Y = np.stack(self.data[self.Y_column][int(low):int(high)])
        
        X_2d = X.reshape(-1, X.shape[-1])
        X_2d = self.scaler.fit_transform(X_2d)
        X = X_2d.reshape(X.shape[:-1] + (-1,))
                                  
        return X,Y
    
    def __len__(self):
        return math.ceil(self.data.shape[0] / self.batch_size)

In [11]:
# this can be done in a for loop but I'll do it the 'redundant' way
# for clarity
input_shape = Input(shape=(513, 25, 1))
# BRANCH VOCALS
x_1 = Conv2D(32, (3,3), padding='same', input_shape=(513, 25, 1))(input_shape)
x_1 = LeakyReLU()(x_1)
x_1 = Conv2D(16, (3,3), padding='same')(x_1)
x_1 = LeakyReLU()(x_1)
x_1 = MaxPooling2D(pool_size=(3,3))(x_1)
x_1 = Dropout(0.25)(x_1)
x_1 = Conv2D(64, (3,3), padding='same')(x_1)
x_1 = LeakyReLU()(x_1)
x_1 = Conv2D(16, (3,3), padding='same')(x_1)
x_1 = LeakyReLU()(x_1)
x_1 = MaxPooling2D(pool_size=(3,3))(x_1)
x_1 = Dropout(0.25)(x_1)
x_1 = Flatten()(x_1)
x_1 = Dense(128)(x_1)
x_1 = LeakyReLU()(x_1)
x_1 = Dropout(0.5)(x_1)
x_1 = Dense(513, activation='sigmoid')(x_1)

In [12]:
# concatenate output layers
merged_output = keras.layers.concatenate([x_1], axis=1)
# connect to single/common input layer
model = Model(input_shape, merged_output)

In [13]:
#sgd = SGD(lr=0.001, decay=1e-6, momentum=0.9, nesterov=True)
opt = keras.optimizers.Adam(learning_rate=0.01)
model.compile(loss=keras.losses.MeanSquaredError(), optimizer=opt, metrics=['accuracy'])

In [8]:
model.summary()

Model: "model"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_1 (InputLayer)        [(None, 513, 25, 1)]      0         
                                                                 
 conv2d (Conv2D)             (None, 513, 25, 32)       320       
                                                                 
 leaky_re_lu (LeakyReLU)     (None, 513, 25, 32)       0         
                                                                 
 conv2d_1 (Conv2D)           (None, 513, 25, 16)       4624      
                                                                 
 leaky_re_lu_1 (LeakyReLU)   (None, 513, 25, 16)       0         
                                                                 
 max_pooling2d (MaxPooling2  (None, 171, 8, 16)        0         
 D)                                                              
                                                             

In [9]:
train_data_gen = dataGenerator("processed_stft_dataset_60.pkl", 'MIXTURE_STFT_SPEC_FRAME', 'VOCALS_STFT_MASK', 5168/16)

In [14]:
model.fit(train_data_gen, epochs=100, shuffle=True)

Epoch 1/100
1506/1506 [==============================] - 3208s 2s/step - loss: 0.3042 - accuracy: 4.8518e-04
Epoch 2/100
 660/1506 [============>.................] - ETA: 32:33 - loss: 0.2949 - accuracy: 6.5672e-05


KeyboardInterrupt



In [ ]:
model.predict(X)

In [8]:
def flatten_by_one_dimension(arr):
    shape = arr.shape
    flattened_shape = (np.prod(shape[:-1]), shape[-1])
    return arr.reshape(flattened_shape)

In [9]:
def prepare_data_2():
    X = []
    Y = []
    for index, song in df_mix['MIXTURE_STFT_SPEC'].items():
        x = df_mix['MIXTURE_STFT_SPEC'][index].T
        x = np.transpose(sliding_window_middle(x, 25), (0, 2, 1))
        print(index)
        for frame in x:
            X.append(frame)
        
        y = df_vocals['VOCALS_STFT_SPEC'][index].T
        for frame in y:
            Y.append(frame)
    #y = np.expand_dims(y, axis=2)
    return X, Y